# Linear regressions on spiracle data, non-parametric and Bayesian

To begin with, we need to import necessary python packages.

In [1]:
import numpy as np
import pandas as pd

import statsmodels.api
import scipy.stats

import bokeh.io
import bokeh.plotting

from Bio import Phylo
import io

import cmdstanpy
import arviz as az

import bebi103

#local .py file for some plotting functions and non-parametric bootstrapping utils
import plotting_utils

bokeh.io.output_notebook()

Loading BokehJS ...

We can now read in the data into a dataframe for analyis.

In [2]:
df = pd.read_csv("./20190322_supp_table_2.csv")

In [3]:
df.loc[df['species'] == 'Mecynorrhina torquata', 'mass (g)'] = 6.875

We take a look at the format for the data.

In [4]:
df['species_underscore'] = [spec.replace(" ", "_") for  spec in df['species']]
df.head()

subfamily                 species sex  mass (g) spiracle  area (mm^2)  \
0  Cetoniinae     Goliathus goliathus   M    16.280        6     0.274408   
1  Cetoniinae     Goliathus goliathus   F    18.150        6     0.134949   
2  Cetoniinae   Coelorrhina hornimani   M     1.130        6     0.212131   
3  Cetoniinae  Dicronorrhina derbyana   M     2.120        6     0.039532   
4  Cetoniinae  Dicronorrhina derbyana   F     2.145        6     0.049701   

   depth (mm)      species_underscore  
0    2.512648     Goliathus_goliathus  
1    1.606189     Goliathus_goliathus  
2    0.553833   Coelorrhina_hornimani  
3    0.473369  Dicronorrhina_derbyana  
4    0.496320  Dicronorrhina_derbyana

For some of this analysis, we will look at the per-species averages for our measurements. To get this, we use a simple aggregate function on the dataframe and take a look at the results.

In [5]:
df_averages = df.groupby(['species', 'species_underscore', 'spiracle'], as_index=False).aggregate(np.average)
df_averages['subfamily'] = df.groupby(['species', 'species_underscore', 'spiracle'], as_index=False).aggregate(max)['subfamily']
df_averages.head()

species     species_underscore spiracle  area (mm^2)  \
0  Coelorrhina hornimani  Coelorrhina_hornimani        1     0.135347   
1  Coelorrhina hornimani  Coelorrhina_hornimani        2     0.084207   
2  Coelorrhina hornimani  Coelorrhina_hornimani        3     0.106693   
3  Coelorrhina hornimani  Coelorrhina_hornimani        4     0.115574   
4  Coelorrhina hornimani  Coelorrhina_hornimani        5     0.119145   

   depth (mm)  mass (g)   subfamily  
0    0.416717      1.13  Cetoniinae  
1    0.451409      1.13  Cetoniinae  
2    0.325444      1.13  Cetoniinae  
3    0.481558      1.13  Cetoniinae  
4    0.506751      1.13  Cetoniinae

Let's take a look at the number of species per subfamily in the data.

In [6]:
species_per_subfam=df_averages.groupby(['subfamily', 'spiracle'], as_index=False).count().groupby('subfamily').aggregate(max).reset_index()[['subfamily', 'species']]
species_per_subfam.columns = ('subfamily', 'subfam_count')
species_per_subfam

subfamily  subfam_count
0  Cetoniinae             6
1  Dynastinae             3
2   Rutelinae             1

In [7]:
df_averages = df_averages.merge(species_per_subfam, on='subfamily')

For our plots, we will log transform the data. We will add a column to the dataframe with the log transformed data. We will also need some transforms of our data, which we will do here.

In [8]:
df_averages['log area (mm^2)'] = np.log10(df_averages['area (mm^2)'])
df_averages['log dist'] = np.log10(df_averages['depth (mm)'])
df_averages['log mass (g)'] = np.log10(df_averages['mass (g)'])
df_averages['log area/dist'] = np.log10(df_averages['area (mm^2)']/df_averages['depth (mm)'])
df_averages['log area^2/dist'] = np.log10(df_averages['area (mm^2)']**2/df_averages['depth (mm)'])

df_averages.head()

species     species_underscore spiracle  area (mm^2)  \
0  Coelorrhina hornimani  Coelorrhina_hornimani        1     0.135347   
1  Coelorrhina hornimani  Coelorrhina_hornimani        2     0.084207   
2  Coelorrhina hornimani  Coelorrhina_hornimani        3     0.106693   
3  Coelorrhina hornimani  Coelorrhina_hornimani        4     0.115574   
4  Coelorrhina hornimani  Coelorrhina_hornimani        5     0.119145   

   depth (mm)  mass (g)   subfamily  subfam_count  log area (mm^2)  log dist  \
0    0.416717      1.13  Cetoniinae             6        -0.868551 -0.380159   
1    0.451409      1.13  Cetoniinae             6        -1.074651 -0.345430   
2    0.325444      1.13  Cetoniinae             6        -0.971862 -0.487524   
3    0.481558      1.13  Cetoniinae             6        -0.937142 -0.317351   
4    0.506751      1.13  Cetoniinae             6        -0.923923 -0.295205   

   log mass (g)  log area/dist  log area^2/dist  
0      0.053078      -0.488392        -1.356943  
1      0.053078      -0.729221        -1.803872  
2      0.053078      -0.484339        -1.456201  
3      0.053078      -0.619790        -1.556932  
4      0.053078      -0.628717        -1.552640

In addition to log transforming the species averaged data, we will do the same for the whole data set.

In [9]:
df['log area (mm^2)'] = np.log10(df['area (mm^2)'])
df['log dist'] = np.log10(df['depth (mm)'])
df['log mass (g)'] = np.log10(df['mass (g)'])
df['log area/dist'] = np.log10(df['area (mm^2)']/df['depth (mm)'])
df['log area^2/dist'] = np.log10(df['area (mm^2)']**2/df['depth (mm)'])
df.head()

subfamily                 species sex  mass (g) spiracle  area (mm^2)  \
0  Cetoniinae     Goliathus goliathus   M    16.280        6     0.274408   
1  Cetoniinae     Goliathus goliathus   F    18.150        6     0.134949   
2  Cetoniinae   Coelorrhina hornimani   M     1.130        6     0.212131   
3  Cetoniinae  Dicronorrhina derbyana   M     2.120        6     0.039532   
4  Cetoniinae  Dicronorrhina derbyana   F     2.145        6     0.049701   

   depth (mm)      species_underscore  log area (mm^2)  log dist  \
0    2.512648     Goliathus_goliathus        -0.561603  0.400132   
1    1.606189     Goliathus_goliathus        -0.869831  0.205797   
2    0.553833   Coelorrhina_hornimani        -0.673395 -0.256621   
3    0.473369  Dicronorrhina_derbyana        -1.403054 -0.324800   
4    0.496320  Dicronorrhina_derbyana        -1.303635 -0.304238   

   log mass (g)  log area/dist  log area^2/dist  
0      1.211654      -0.961735        -1.523338  
1      1.258877      -1.075628        -1.945459  
2      0.053078      -0.416774        -1.090169  
3      0.326336      -1.078254        -2.481309  
4      0.331427      -0.999397        -2.303033

With our data in this format, we can build simple model for our regression. To do this, we will write a statistical model for the data. We choose a normal distribution with mean given by a simple linear function (with slope $a$ and intercept $b$), and homoscedastic variance $\sigma$. For our priors, we will take a normal distribution for the slope with mean given by the slope value representing isometric scaling in the log-log space, and standard deviation of $0.3$. This encodes our prior expectation that isometry is the most common/likely outcome for morphological features. If they scale uniformly with one another, we would see isometry. The variance term on this prior gives a broad but reasonable range of potential values for the parameter around the isometric value. This prior is hence weakly informative, fairly encoding our prior expectation without constraining the ability of our data to inform the parameter value. For the intercept, we expect a small value for spiracle dimensions of a 1g insect (what the intercept of the log mass x axis represents), so we put this mean at around 1/10th of a square mm for area (mean of -1 in log space), with a standard deviation of 1. Hence ~95% of the probability mass for this prior goes from ~100 times smaller to ~100 times larger than this mean. Once again, this is a pretty broad distribution so shouldn't drag the parameter estimates much, but does encode our prior intuition of what we expect from beetle spiracle dimensions. For the prior on the $\sigma$ term for the normal distribution, we take a half normal ($\sigma$ must be positive), with mean at zero and standard deviation of 1, once again this allows for a wide range of values for sigma while also encoding our expectation that morphological measures shouldn't have extreme variation on a log scale. This gives the following model:

\begin{align}
f_{\mu}(x_i; a, b) &= ax_i + b \\
b &\sim \text{Norm}(-1, 1) \\
a &\sim \text{Norm}(\mathrm{isometry}, 0.3)\\ [\mathrm{isometry_{area}=2/3, \, isometry_{depth}=1/3},& \, \mathrm{isometry_{area/depth}}=1/3, \, \mathrm{isometry_{area^2/depth}}=1]\\
\sigma &\sim \text{HalfNorm}(0, 1)\\
y_i &\sim \text{Normal}\left(f_\mu(x_i; a, b), \sigma\right)
\end{align}


We will do a quick prior-predictive check of this model to make sure it gives reasonable potential datasets.

In [32]:
x = df_averages.sort_values('mass (g)').loc[df_averages['spiracle'] == '1', 'log mass (g)'].values
size = 1000
lines = []
for a, b, sigma in zip(np.random.normal(0.67,0.3, size=size), np.random.normal(-1,1,size=size), np.abs(np.random.normal(1,size=size))):
    lines.append(np.random.normal(a*x+b, sigma))
    
p = bokeh.plotting.figure(plot_height=250, x_axis_label='mass', y_axis_label='spiracle dimension')
[p.line(x, y, alpha=0.05) for y in lines]
bokeh.io.show(p)

This looks good! The proposed model gives a slight upward slope and a nice wide range of values for both the slope and intercept based on the priors. The data should be able to inform the parameter values well based on this model. We are now ready to sample to get parameter estimates! We do this below. In addition to sampling, we also produce some plots of the model outputs given the sampled parameters (i.e. the posterior samples as well as samples from the posterior predictive distribution). 

In [10]:
all_summaries = {}
all_regressions = {}
N_ppc = 200
for morphs, iso in zip(['log area (mm^2)', 'log dist', 'log area/dist', 'log area^2/dist'], [0.67, 0.33, 0.33, 1.0]):

    sigmas = []
    slopes = []
    intercepts = []
    summaries = {}
    plots = []
    for spir in ['S', 'T', '1', '2', '3', '4', '5', '6']:
        x = df_averages.sort_values('mass (g)').loc[df_averages['spiracle'] == spir, 'log mass (g)'].values
        y = df_averages.sort_values('mass (g)').loc[df_averages['spiracle'] == spir, morphs].values

        x_ppc = np.linspace(x.min(), x.max(), N_ppc)
        
        data = {
            "N": len(x),
            "x": x,
            "y": y,
            "priora": iso,
            "x_ppc": x_ppc,
            'N_ppc': N_ppc,
        }

        sm = cmdstanpy.CmdStanModel(stan_file='spiracle_regression.stan')

        samples = sm.sample(data=data, sampling_iters=1000, chains=4)

        samples = az.from_cmdstanpy(posterior=samples, posterior_predictive=["y_ppc"])
        bebi103.stan.check_all_diagnostics(samples, var_names=['b', 'a', 'sigma'])
        sigmas.append(samples.posterior['sigma'].values.ravel())
        slopes.append(samples.posterior['a'].values.ravel())
        intercepts.append(samples.posterior['b'].values.ravel())
        summaries[spir] = az.summary(samples, var_names=['b', 'a', 'sigma'])
        summaries[spir]['median'] = [np.median(samples.posterior['b'].values.ravel()),
                                     np.median(samples.posterior['a'].values.ravel()),
                                     np.median(samples.posterior['sigma'].values.ravel())]
        plots.append(plotting_utils.plot_regression_comparison(df, df_averages, x, spir, morphs, samples, iso, x_ppc, circle_size=4, line_width=1, circle_alpha=1, size=230))
        
    all_regressions[morphs] = plots
    all_summaries[morphs] = summaries

INFO:cmdstanpy:found newer exe file, not recompiling
INFO:cmdstanpy:compiled model file: C:/Users/jwagne/git/spiracle_scaling/spiracle_regression.exe
INFO:cmdstanpy:start chain 1
INFO:cmdstanpy:start chain 2
INFO:cmdstanpy:start chain 3
INFO:cmdstanpy:start chain 4
INFO:cmdstanpy:finish chain 4
INFO:cmdstanpy:finish chain 1
INFO:cmdstanpy:finish chain 2
INFO:cmdstanpy:finish chain 3
INFO:cmdstanpy:found newer exe file, not recompiling
INFO:cmdstanpy:compiled model file: C:/Users/jwagne/git/spiracle_scaling/spiracle_regression.exe
INFO:cmdstanpy:start chain 1
INFO:cmdstanpy:start chain 2
INFO:cmdstanpy:start chain 3
INFO:cmdstanpy:start chain 4


Effective sample size looks reasonable for all parameters.
Rhat looks reasonable for all parameters.
0 of 4000 (0.0%) iterations ended with a divergence.
0 of 4000 (0.0%) iterations saturated the maximum tree depth of 10.
E-BFMI indicated no pathological behavior.


INFO:cmdstanpy:finish chain 4
INFO:cmdstanpy:finish chain 1
INFO:cmdstanpy:finish chain 2
INFO:cmdstanpy:finish chain 3
INFO:cmdstanpy:found newer exe file, not recompiling
INFO:cmdstanpy:compiled model file: C:/Users/jwagne/git/spiracle_scaling/spiracle_regression.exe
INFO:cmdstanpy:start chain 1
INFO:cmdstanpy:start chain 2
INFO:cmdstanpy:start chain 3
INFO:cmdstanpy:start chain 4


Effective sample size looks reasonable for all parameters.
Rhat looks reasonable for all parameters.
0 of 4000 (0.0%) iterations ended with a divergence.
0 of 4000 (0.0%) iterations saturated the maximum tree depth of 10.
E-BFMI indicated no pathological behavior.


INFO:cmdstanpy:finish chain 3
INFO:cmdstanpy:finish chain 2
INFO:cmdstanpy:finish chain 1
INFO:cmdstanpy:finish chain 4
INFO:cmdstanpy:found newer exe file, not recompiling
INFO:cmdstanpy:compiled model file: C:/Users/jwagne/git/spiracle_scaling/spiracle_regression.exe
INFO:cmdstanpy:start chain 1
INFO:cmdstanpy:start chain 2
INFO:cmdstanpy:start chain 3
INFO:cmdstanpy:start chain 4


...

Effective sample size looks reasonable for all parameters.
Rhat looks reasonable for all parameters.
0 of 4000 (0.0%) iterations ended with a divergence.
0 of 4000 (0.0%) iterations saturated the maximum tree depth of 10.
E-BFMI indicated no pathological behavior.


INFO:cmdstanpy:finish chain 2
INFO:cmdstanpy:finish chain 1
INFO:cmdstanpy:finish chain 4
INFO:cmdstanpy:finish chain 3
INFO:cmdstanpy:found newer exe file, not recompiling
INFO:cmdstanpy:compiled model file: C:/Users/jwagne/git/spiracle_scaling/spiracle_regression.exe
INFO:cmdstanpy:start chain 1
INFO:cmdstanpy:start chain 2
INFO:cmdstanpy:start chain 3
INFO:cmdstanpy:start chain 4


Effective sample size looks reasonable for all parameters.
Rhat looks reasonable for all parameters.
0 of 4000 (0.0%) iterations ended with a divergence.
0 of 4000 (0.0%) iterations saturated the maximum tree depth of 10.
E-BFMI indicated no pathological behavior.


INFO:cmdstanpy:finish chain 2
INFO:cmdstanpy:finish chain 1
INFO:cmdstanpy:finish chain 4
INFO:cmdstanpy:finish chain 3


Effective sample size looks reasonable for all parameters.
Rhat looks reasonable for all parameters.
0 of 4000 (0.0%) iterations ended with a divergence.
0 of 4000 (0.0%) iterations saturated the maximum tree depth of 10.
E-BFMI indicated no pathological behavior.


With samples for all the parameters and for all the spiracles/morphological features of interest in hand, we can now generate a plot for some summary stats about the data. We will also compute similar estimates for regression features of interest using a non-parametric bootstrapping approach for comparison.

In [38]:
plots = []
for morphs, iso, heading in zip(['log area (mm^2)', 'log dist', 'log area/dist', 'log area^2/dist'], [0.67, 0.33, 0.33, 1.0], ['Area', 'Depth', 'Diffusive', 'Advective']):
    #print(morphs)
    summaries = all_summaries[morphs]
    for var, yax, var_title in zip(['a', 'b', 'sigma'], ['log-log slope', 'intercept (mm^2)', 'log-log sigma'], ['slope', 'intercept', 'variance']):
        p = bokeh.plotting.figure(plot_height=200, plot_width=300, x_range=['S', 'T', '1', '2', '3', '4', '5', '6'], title=heading + ', Median ± HPD for ' + var_title, y_axis_label=yax, x_axis_label='Spiracle')#, y_axis_type='log')
        p = bokeh.plotting.figure(plot_height=200, plot_width=300, x_range=['S', 'T', '1', '2', '3', '4', '5', '6'])
        p.xaxis.visible = False
        p.outline_line_color = None
        p.yaxis.minor_tick_line_color = None
        p.xaxis.minor_tick_line_color = None
        if var == 'a':
                p.line([-10, 100], [iso, iso], color='black', line_width=2, line_alpha=1)
        for i, spir in enumerate(['S', 'T', '1', '2', '3', '4', '5', '6']):
            CI_a, CI_b, CI_σ, slope, intercept, σ = plotting_utils.make_CIs(df_averages, morphs, spir)
            
            if var == 'b':
                c = 1
                if morphs == 'log area/dist':
                    c = 0.178*404*(1/10)
                elif morphs == 'log area^2/dist':
                    c = (1/(3.1415*8*1.86*(10**(-8))))*(0.1**3)
                p.line([spir, spir], c*(10**np.array([summaries[spir].loc[var]['hpd_3%'], summaries[spir].loc[var]['hpd_97%']])), color='grey', line_width=7, alpha=0.75)
                p.line([spir, spir], c*(10**CI_b), color='black', line_width=2, alpha=0.75)
                p.diamond([spir,],   c*(10**summaries[spir].loc[var]['median']), color='white', size=9, alpha=1)
                p.diamond([spir,],   c*(10**intercept), color='black', size=5)
            elif var == 'a':
                p.line([spir, spir], [summaries[spir].loc[var]['hpd_3%'], summaries[spir].loc[var]['hpd_97%']], color='grey', line_width=7, alpha=0.75)
                p.line([spir, spir], CI_a, color='black', line_width=2, alpha=0.75)
                p.diamond([spir,], summaries[spir].loc[var]['median'], color='white', size=9, alpha=1)
                p.diamond([spir,], slope, color='black', size=5)
            else:
                p.line([spir, spir], [summaries[spir].loc[var]['hpd_3%'], summaries[spir].loc[var]['hpd_97%']], color='grey', line_width=7, alpha=0.75)
                p.line([spir, spir], CI_σ, color='black', line_width=2, alpha=0.75)
                p.diamond([spir,], summaries[spir].loc[var]['median'], color='white', size=9, alpha=1)
                p.diamond([spir,], σ, color='black', size=5)

        p.xgrid.grid_line_color = None
        #p.ygrid.grid_line_color = None
        p.output_backend = 'svg'
        plots.append(p)
        #bokeh.io.show(p)
        
print("FOR ALL PLOTS: White diamond is median Bayesian parameter sample, grey box is 3%-97% highest posterior density interval for parameter samples")
print("FOR ALL PLOTS: Black diamond is median summary statistic for non-parametric bootstrapping on OLS, black line is 2.5%-97.5% percentile for bootstrapped summary stat")
print('Area regressions (log-log slope, intercept (mm^2), log-log σ)')
bokeh.io.show(bokeh.layouts.gridplot(plots[0:3], ncols=3))
print('Depth regressions (log-log slope, intercept (mm), log-log σ)')
bokeh.io.show(bokeh.layouts.gridplot(plots[3:6], ncols=3))
print('Area/Depth regressions (log-log slope, intercept (G_diff), log-log σ)')
bokeh.io.show(bokeh.layouts.gridplot(plots[6:9], ncols=3))
print('Area^2/Depth regressions (log-log slope, intercept (G_adv), log-log σ)')
bokeh.io.show(bokeh.layouts.gridplot(plots[9:12], ncols=3))

FOR ALL PLOTS: White diamond is median Bayesian parameter sample, grey box is 3%-97% highest posterior density interval for parameter samples
FOR ALL PLOTS: Black diamond is median summary statistic for non-parametric bootstrapping on OLS, black line is 2.5%-97.5% percentile for bootstrapped summary stat
Area regressions (log-log slope, intercept (mm^2), log-log σ)


Depth regressions (log-log slope, intercept (mm), log-log σ)


Area/Depth regressions (log-log slope, intercept (G_diff), log-log σ)


Area^2/Depth regressions (log-log slope, intercept (G_adv), log-log σ)


Great! With these summary stats in hand, we can also do some plots of all of these regressions themselves. Note that for all of these plots the blue ranges show the range of regression output values (either from sampling or bootstrapping) at the 2.5th-97.5th percentiles. Central line is the 45th-55th percentile range for Bayesian regression values, or the OLS line with non-resampled data for the the bootstrap regression plots. The two grey regions for the Bayesian regressions are the 95th and 80th percentile ranges for the posterior predictive distribution for the model. 

---

## Plot for species averaged mass vs species averaged spiracle area (log transformed)

In [16]:
print("Bayesian regression:")
bokeh.io.show(bokeh.layouts.gridplot(all_regressions['log area (mm^2)'], ncols=4))
print("Non-parametric bootstrapping:")
plotting_utils.make_plot(df_averages, 'log area (mm^2)', 2/3)

Bayesian regression:


Non-parametric bootstrapping:


---

## Species averaged mass vs species averaged spiracle depth (log transformed)

In [19]:
print("Bayesian regression:")
bokeh.io.show(bokeh.layouts.gridplot(all_regressions['log dist'], ncols=4))
print("Non-parametric bootstrapping:")
plotting_utils.make_plot(df_averages, 'log dist', 1/3)

Bayesian regression:


Non-parametric bootstrapping:


---

## Species averaged mass vs $\frac{\mathrm{species\,averaged\,area}}{\mathrm{species\,averaged\,depth}}$ (log transformed)

In [20]:
print("Bayesian regression:")
bokeh.io.show(bokeh.layouts.gridplot(all_regressions['log area/dist'], ncols=4))
print("Non-parametric bootstrapping:")
plotting_utils.make_plot(df_averages, 'log area/dist', 1/3)

Bayesian regression:


Non-parametric bootstrapping:


---

## Species averaged mass vs $\frac{(\mathrm{species\,averaged\,area})^2}{\mathrm{species\,averaged\,depth}}$ (log transformed)

In [21]:
print("Bayesian regression:")
bokeh.io.show(bokeh.layouts.gridplot(all_regressions['log area^2/dist'], ncols=4))
print("Non-parametric bootstrapping:")
plotting_utils.make_plot(df_averages, 'log area^2/dist', 1)

Bayesian regression:


Non-parametric bootstrapping:


In [440]:
df_test = df_averages.copy()
df_test['area/depth'] = (df_averages['area (mm^2)']/df_averages['depth (mm)'])/10
df_test['area^2/depth'] = ((df_averages['area (mm^2)']**2/df_averages['depth (mm)']))/(1000*1000*1000)

In [441]:
df_test['g_diff'] = df_test['area/depth']*0.178*404
df_test['g_adv'] = df_test['area^2/depth']*(1/(8*1.86*10**(-8)))

In [442]:
df_test.groupby('species').sum().reset_index()

species  area (mm^2)  depth (mm)  mass (g)  subfam_count  \
0   Coelorrhina hornimani     1.103714    3.522890    9.0400            48   
1   Cyclocephala borealis     0.159740    1.778172    0.8508            24   
2  Dicronorrhina derbyana     0.760657    3.875291   17.0600            48   
3       Dynastes hercules     4.365984    9.712252  210.8000            24   
4      Eudicella euthalia     1.104579    4.102301   17.4680            48   
5     Goliathus goliathus     6.184834   10.961348  138.6550            48   
6   Mecynorrhina torquata     2.573181    5.903761   55.0000            48   
7        Popilia japonica     0.072902    1.442668    1.0496             8   
8    Protaetia orientalis     0.637364    2.241707   11.0000            48   
9   Trypoxylus dichotomus     1.007904    5.790601   51.3192            24   

   log area (mm^2)  log dist  log mass (g)  log area/dist  log area^2/dist  \
0        -7.102671 -2.913611      0.424628      -4.189060       -11.291732   
1       -15.063659 -5.263023     -7.788166      -9.800637       -24.864296   
2        -9.096369 -2.587199      2.631112      -6.509171       -15.605540   
3        -3.337818  0.375281     11.366245      -3.713099        -7.050916   
4        -7.979423 -2.370173      2.713226      -5.609250       -13.588673   
5        -2.236641  0.996939      9.910226      -3.233580        -5.470221   
6        -6.095399 -1.190792      6.698182      -4.904607       -11.000006   
7       -17.692325 -6.005029     -7.056529     -11.687296       -29.379621   
8        -9.518070 -4.492271      1.106422      -5.025798       -14.543868   
9        -8.243958 -1.283270      6.457519      -6.960688       -15.204645   

   area/depth  area^2/depth     g_diff     g_adv  
0    0.266338  4.324003e-10  19.152881  0.002906  
1    0.080373  2.479719e-11   5.779752  0.000167  
2    0.198596  4.303639e-10  14.281452  0.002892  
3    0.552337  5.347454e-09  39.719626  0.035937  
4    0.264733  8.556551e-10  19.037471  0.005750  
5    0.537985  7.793716e-09  38.687586  0.052377  
6    0.380916  3.655382e-09  27.392434  0.024566  
7    0.043588  9.757197e-12   3.134528  0.000066  
8    0.241444  3.062032e-10  17.362721  0.002058  
9    0.190437  4.532233e-10  13.694691  0.003046

In [443]:
df_summed = df_test.groupby('species').median().reset_index()
df_summed['g_diff'] = df_test.groupby('species').sum().reset_index()['g_diff']
df_summed['a_diff'] = df_test.groupby('species').sum().reset_index()['area/depth']
df_summed['g_adv'] = df_test.groupby('species').sum().reset_index()['g_adv']


In [444]:
df_summed

species  area (mm^2)  depth (mm)  mass (g)  subfam_count  \
0   Coelorrhina hornimani     0.117359    0.465658    1.1300             6   
1   Cyclocephala borealis     0.024597    0.214594    0.1077             3   
2  Dicronorrhina derbyana     0.068841    0.497511    2.1325             6   
3       Dynastes hercules     0.559997    0.998058   26.3500             3   
4      Eudicella euthalia     0.078973    0.527117    2.1835             6   
5     Goliathus goliathus     0.432050    1.228101   17.2150             6   
6   Mecynorrhina torquata     0.150779    0.624893    6.8750             6   
7        Popilia japonica     0.005652    0.169834    0.1312             1   
8    Protaetia orientalis     0.059411    0.295024    1.3750             6   
9   Trypoxylus dichotomus     0.107295    0.700316    6.4149             3   

   log area (mm^2)  log dist  log mass (g)  log area/dist  log area^2/dist  \
0        -0.930532 -0.332137      0.053078      -0.554091        -1.504421   
1        -1.609215 -0.668964     -0.967784      -0.925175        -2.534390   
2        -1.165905 -0.303338      0.328889      -0.876124        -2.027904   
3        -0.266835 -0.002274      1.420781      -0.237868        -0.493665   
4        -1.102595 -0.278099      0.339153      -0.848799        -1.952646   
5        -0.388428  0.088816      1.235907      -0.488871        -0.908839   
6        -0.832350 -0.204378      0.837273      -0.681502        -1.481668   
7        -2.248248 -0.770173     -0.882066      -1.542499        -3.762709   
8        -1.226356 -0.530238      0.138303      -0.646953        -1.861025   
9        -0.970789 -0.156481      0.807190      -0.797925        -1.753284   

   area/depth  area^2/depth     g_diff     g_adv    a_diff  
0    0.028240  3.149567e-11  19.152881  0.002906  0.266338  
1    0.011906  2.924481e-12   5.779752  0.000167  0.080373  
2    0.013301  9.518755e-12  14.281452  0.002892  0.198596  
3    0.058692  3.558352e-10  39.719626  0.035937  0.552337  
4    0.014206  1.117263e-11  19.037471  0.005750  0.264733  
5    0.036377  1.762062e-10  38.687586  0.052377  0.537985  
6    0.020824  3.462794e-11  27.392434  0.024566  0.380916  
7    0.002881  1.763960e-13   3.134528  0.000066  0.043588  
8    0.022590  1.377136e-11  17.362721  0.002058  0.241444  
9    0.016269  1.857460e-11  13.694691  0.003046  0.190437

In [445]:
p = bokeh.plotting.figure(y_axis_type='log', plot_height=300)

p.line([-1, 1.5], [21, 21])

p.scatter(df_summed['log mass (g)'], 
          (90*((10**(3.20 + 0.75*df_summed['log mass (g)']))*(1/20.7)*(1/24.5))/(df_summed['g_diff']*2)))

p.scatter(df_summed['log mass (g)'], 
          (8*((10**(3.20 + 0.75*df_summed['log mass (g)']))*(1/20.7)*(1/24.5))/(df_summed['g_diff']*2)))

p.scatter(df_summed['log mass (g)'], 
          (1*((10**(3.20 + 0.75*df_summed['log mass (g)']))*(1/20.7)*(1/24.5))/(df_summed['g_diff']*2)))

bokeh.io.show(p)

In [278]:
p = bokeh.plotting.figure(plot_height=300)
p.circle(df_summed['log mass (g)'], np.log10(df_summed['g_diff']*2/10))
bokeh.io.show(p)

In [273]:
p = bokeh.plotting.figure(plot_height=300)
p.circle(df_summed['log mass (g)'], np.log10(df_summed['g_adv']*2))
bokeh.io.show(p)

In [122]:
spir = '6'
p = bokeh.plotting.figure(x_axis_label='log mass', y_axis_label='log area')


############################################
############################################
############################################

x = np.linspace(x.min(), x.max(), 200)
# y-values of each point
y = samples.posterior_predictive['y_ppc'][0].values

# Compute the 2.5th and 97.5th percentiles
low, high = np.percentile(y, [2.5, 97.5], axis=0)

p1 = np.append(x, x[::-1])
p2 = np.append(low, high[::-1])

p.patch(p1, p2, alpha=p_alpha, color='grey')

# Compute the 10th and 90th percentiles
low, high = np.percentile(y, [10, 90], axis=0)

p1 = np.append(x, x[::-1])
p2 = np.append(low, high[::-1])

p.patch(p1, p2, alpha=p_alpha, color='grey')

# Compute the 20th and 80th percentiles
low, high = np.percentile(y, [20, 80], axis=0)

p1 = np.append(x, x[::-1])
p2 = np.append(low, high[::-1])

p.patch(p1, p2, alpha=p_alpha, color='grey')



p_alpha = 0.15
# x-values
x = np.linspace(x.min(), x.max(), 200)

# y-values of each point
y = np.outer(samples.posterior['a'].values[0], x) + np.stack([samples.posterior['b'].values[0]]*200, axis=1)

# Compute the 2.5th and 97.5th percentiles
low, high = np.percentile(y, [2.5, 97.5], axis=0)

p1 = np.append(x, x[::-1])
p2 = np.append(low, high[::-1])

p.patch(p1, p2, alpha=p_alpha, color='black')

# Compute the 10th and 90th percentiles
low, high = np.percentile(y, [10, 90], axis=0)

p1 = np.append(x, x[::-1])
p2 = np.append(low, high[::-1])

p.patch(p1, p2, alpha=p_alpha, color='black')

# Compute the 20th and 80th percentiles
low, high = np.percentile(y, [20, 80], axis=0)

p1 = np.append(x, x[::-1])
p2 = np.append(low, high[::-1])

p.patch(p1, p2, alpha=p_alpha, color='black')


############################################
############################################
############################################

x = df_averages.sort_values('mass (g)').loc[df_averages['spiracle'] == spir, 'log mass (g)'].values
y = df_averages.sort_values('mass (g)').loc[df_averages['spiracle'] == spir, morphs].values


Y = df.sort_values('mass (g)').loc[df['spiracle'] == spir, morphs].values
X = df.sort_values('mass (g)').loc[df['spiracle'] == spir, 'log mass (g)'].values
X = statsmodels.api.add_constant(X)
model = statsmodels.api.OLS(Y,X)
results = model.fit()
results.params


p.circle(df.sort_values('mass (g)').loc[df['spiracle'] == spir, 'log mass (g)'].values,
         df.sort_values('mass (g)').loc[df['spiracle'] == spir, morphs].values, color='black', size=15, alpha=0.3, fill_color='green')

p.line(np.linspace(x.min(), x.max(), 200),
       results.params[1]*np.linspace(x.min(), x.max(), 200) + results.params[0],
       line_width=5, line_dash='dashed', color='orange', alpha=0.3, legend_label='OLS all data')


Y = y
X = x
X = statsmodels.api.add_constant(X)
model = statsmodels.api.OLS(Y,X)
results = model.fit()
results.params

p.line(np.linspace(x.min(), x.max(), 200),
       az.summary(samples, var_names=['b', 'a'])['mean']['a']*np.linspace(x.min(), x.max(), 200) + az.summary(samples, var_names=['b', 'a'])['mean']['b'],
       line_width=5, color='black', legend_label='Average parameter MCMC reggression')

p.line(np.linspace(x.min(), x.max(), 200),
       results.params[1]*np.linspace(x.min(), x.max(), 200) + results.params[0],
       line_width=5, line_dash='dashed', color='grey', legend_label='OLS averages')

p.circle(x, y, color='black', size=15, alpha=0.5, fill_color='red')

p.legend.location = 'bottom_right'

bokeh.io.show(p)

In [108]:
x = np.linspace(x.min(), x.max(), 200)

# y-values of each point
y = np.outer(samples.posterior['a'].values[0], x) + np.stack([samples.posterior['b'].values[0]]*200, axis=1)

In [110]:
y.shape

(1000, 200)

In [115]:
samples.posterior_predictive['y_ppc'][0].values.shape

(1000, 200)